# Coursera - IBM Data Science Capstone Project

## Where should I open an pizza place in Melbourne, Australia?

### Steps:

#### 1) Scrape a wikipedia page and make Pandas dataframe of Melbourne suburbs.
#### 2) Get the latlongs of each suburb.
#### 3) Get neighbourhoods' venue data using Foursquare API
#### 4) Find and explore clusters
#### 5) Select the most suitable cluster

In [1]:
import pandas as pd
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import numpy as np

import json

!pip install --upgrade geocoder
from geopy.geocoders import Nominatim
import geocoder

import requests
from bs4 import BeautifulSoup

from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

!pip install folium
import folium

print('DONE!!!')

     |████████████████████████████████| 102kB 12.1MB/s ta 0:00:01
     |████████████████████████████████| 92kB 15.0MB/s eta 0:00:01
DONE!!!


### Scrape a wikipedia page and make Pandas dataframe of Melbourne suburbs.

In [2]:
df = pd.read_html('https://en.wikipedia.org/wiki/List_of_Melbourne_suburbs')

In [3]:
df = df[0]

In [4]:
df = df['Suburb']

In [5]:
df = df.to_frame()

In [6]:
df = df.drop_duplicates()

In [7]:
df = df.sort_values(['Suburb'], ascending = True)

In [8]:
df.head()

Suburb
478    Abbotsford
341    Aberfeldie
297       Aintree
342  Airport West
46      Albanvale

### Get the latlongs of each suburb

In [9]:
# Function to get coordinates
def get_latlng(suburb):
    lat_lng_coords = None
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{},Melbourne,Australia'.format(suburb))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [10]:
mel_coor = [get_latlng(suburb) for suburb in df['Suburb'].tolist()]
mel_coor

[[-37.80305999999996, 144.99718000000007],
 [-37.759289999999964, 144.8958],
 [-37.939103574873755, 145.18691188642688],
 [-37.711869999999976, 144.88697000000002],
 [-37.744599999999934, 144.77025000000003],
 [-37.84403999999995, 144.95126000000005],
 [-37.775559999999984, 144.8156100000001],
 [-37.77941999999996, 145.02503000000002],
 [-37.863819999999976, 144.82482000000005],
 [-37.87176999999997, 144.77760000000012],
 [-37.830469999999934, 144.84134000000006],
 [-37.77204999999998, 144.79997000000003],
 [-37.85550999999998, 145.02089],
 [-37.856676813467296, 144.87123077675622],
 [-37.77545999999995, 144.91556000000003],
 [-37.863099999999974, 145.07716000000005],
 [-37.86690999999996, 145.10292000000004],
 [-38.026659999999936, 145.10202000000004],
 [-38.018219999999985, 145.11359000000004],
 [-37.66990999999996, 144.88792],
 [-37.76718999999997, 144.8641100000001],
 [-37.76749427109016, 145.2533640284895],
 [-37.87515, 145.30629600000003],
 [-37.86902999999995, 144.99565000000007

In [11]:
mel_coor_df = pd.DataFrame(mel_coor, columns=['Latitude', 'Longitude'])

In [12]:
df['Latitude'] = mel_coor_df['Latitude']
df['Longitude'] = mel_coor_df['Longitude']

In [13]:
df = df.dropna()

In [14]:
df.shape

(539, 3)

### Create a map of Melbourne (incl. all suburbs)

In [15]:
address = 'Melbourne,Australia'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Melbourne, Australia is {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Melbourne, Australia is -37.8142176, 144.9631608.


In [16]:
map_melb = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, Suburb in zip(df['Latitude'], df['Longitude'], df['Suburb']):
    label = '{}'.format(Suburb)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_melb)  
    
map_melb

In [19]:
CLIENT_ID = '5AECJKA5IT2CP1TT0V4ZWFCH0LGD522GOXBNFBZKKZRIFRI4' # your Foursquare ID
CLIENT_SECRET = 'DKNYUPAE43AB0QABOOH0TXWF3ARJQ0KGYHPAXY1TZWQ3QOBS' # your Foursquare Secret
VERSION = '20190822'

#### Top 100 venues that are within a radius of 5000 meters

In [20]:
radius = 5000
LIMIT = 50

venues = []

for lat, long, suburb in zip(df['Latitude'], df['Longitude'], df['Suburb']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()['response']['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            suburb,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [23]:
# converting the venues list into new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Suburb', 'Latitude', 'Longitude', 'Venue_Name', 'Venue_Latitude', 'Venue_Longitude', 'Venue_Category']

print(venues_df.shape)
venues_df.head()

(23471, 7)


Suburb   Latitude   Longitude                      Venue_Name  \
0  Abbotsford -37.776843  145.029515                    Mr Wednesday   
1  Abbotsford -37.776843  145.029515                  Fifteen Pounds   
2  Abbotsford -37.776843  145.029515                    Dan Murphy's   
3  Abbotsford -37.776843  145.029515                        Ora Cafe   
4  Abbotsford -37.776843  145.029515  Paladarr Thai Issan Restaurant   

   Venue_Latitude  Venue_Longitude   Venue_Category  
0      -37.778989       145.024190             Café  
1      -37.779379       145.017205             Café  
2      -37.779862       145.032971     Liquor Store  
3      -37.795988       145.036023             Café  
4      -37.778499       145.032466  Thai Restaurant

In [24]:
# Venues per suburb

venues_df.groupby(['Suburb']).count()

Latitude  Longitude  Venue_Name  \
Suburb                                                                
Abbotsford                                50         50          50   
Aberfeldie                                35         35          35   
Aintree                                   50         50          50   
Airport West                              23         23          23   
Albanvale                                 50         50          50   
Albert Park                               50         50          50   
Albion                                    11         11          11   
Alphington                                50         50          50   
Altona                                    50         50          50   
Altona Meadows                            25         25          25   
Altona North                              50         50          50   
Ardeer                                    50         50          50   
Armadale                                  50         50          50   
Arthurs Seat                              50         50          50   
Ascot Vale                                24         24          24   
Ashburton                                 43         43          43   
Ashwood                                   50         50          50   
Aspendale                                 50         50          50   
Aspendale Gardens                         50         50          50   
Attwood                                   50         50          50   
Avondale Heights                           7          7           7   
Avonsleigh                                50         50          50   
Badger Creek                              50         50          50   
Balaclava                                 50         50          50   
Balnarring                                44         44          44   
Balnarring Beach                          50         50          50   
Balwyn                                    39         39          39   
Balwyn North                               6          6           6   
Bangholme                                 50         50          50   
Baxter                                    50         50          50   
Bayles                                    46         46          46   
Bayswater                                 43         43          43   
Bayswater North                           50         50          50   
Beaconsfield                              50         50          50   
Beaconsfield Upper                        46         46          46   
Beaumaris                                 50         50          50   
Beenak                                    10         10          10   
Belgrave                                  50         50          50   
Belgrave Heights                          50         50          50   
Belgrave South                            50         50          50   
Bellfield                                 50         50          50   
Bend of Islands                           50         50          50   
Bentleigh                                 50         50          50   
Bentleigh East                            14         14          14   
Berwick                                   50         50          50   
Beveridge                                 50         50          50   
Big Pats Creek                            15         15          15   
Bittern                                   50         50          50   
Black Rock                                50         50          50   
Blackburn                                 50         50          50   
Blackburn North                           50         50          50   
Blackburn South                           50         50          50   
Blairgowrie                               50         50          50   
Blind Bight                                8          8           8   
Bonbeach                                  50         50     

#### No. of unique categories from venues

In [25]:
print('There are {} unique categories.'.format(len(venues_df['Venue_Category'].unique())))

There are 281 unique categories.


#### List of categories

In [26]:
venues_df['Venue_Category'].unique()[:50]

array(['Café', 'Liquor Store', 'Thai Restaurant', 'Lebanese Restaurant',
       'Park', 'Pizza Place', 'Indian Restaurant', 'Bar', 'Movie Theater',
       'Gourmet Shop', 'Golf Course', 'Vietnamese Restaurant', 'Bakery',
       'Ice Cream Shop', 'Rock Club', 'Falafel Restaurant',
       'Greek Restaurant', 'Vegetarian / Vegan Restaurant', 'Farm',
       'Gastropub', 'Climbing Gym', 'Cultural Center', 'Grocery Store',
       'Japanese Restaurant', 'French Restaurant',
       'Australian Restaurant', 'Music Venue', 'Italian Restaurant',
       'Restaurant', 'Scenic Lookout', 'Beach',
       'Middle Eastern Restaurant', 'Hotel Bar', 'Burger Joint',
       'Dumpling Restaurant', 'Supermarket', 'Theater', 'Gas Station',
       'Deli / Bodega', 'Fast Food Restaurant', 'Pharmacy',
       'Other Great Outdoors', 'Farmers Market', 'Field', 'Garden',
       'Asian Restaurant', 'Zoo', 'Exhibit', 'Pub', 'Pool'], dtype=object)

### Analyzing each suburb


In [27]:
# one hot encoding
melb_onehot = pd.get_dummies(venues_df[['Venue_Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
melb_onehot['Suburb'] = venues_df['Suburb'] 

# move neighborhood column to the first column
fixed_columns = [melb_onehot.columns[-1]] + list(melb_onehot.columns[:-1])
melb_onehot = melb_onehot[fixed_columns]

print(melb_onehot.shape)
melb_onehot.head()

(23471, 282)


Suburb  Afghan Restaurant  African Restaurant  Airport  Airport Lounge  \
0  Abbotsford                  0                   0        0               0   
1  Abbotsford                  0                   0        0               0   
2  Abbotsford                  0                   0        0               0   
3  Abbotsford                  0                   0        0               0   
4  Abbotsford                  0                   0        0               0   

   Airport Service  American Restaurant  Antique Shop  Arcade  \
0                0                    0             0       0   
1                0                    0             0       0   
2                0                    0             0       0   
3                0                    0             0       0   
4                0                    0             0       0   

   Argentinian Restaurant  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0                       0            0                    0                 0   
1                       0            0                    0                 0   
2                       0            0                    0                 0   
3                       0            0                    0                 0   
4                       0            0                    0                 0   

   Athletics & Sports  Australian Restaurant  Auto Garage  Auto Workshop  \
0                   0                      0            0              0   
1                   0                      0            0              0   
2                   0                      0            0              0   
3                   0                      0            0              0   
4                   0                      0            0              0   

   BBQ Joint  Bagel Shop  Bakery  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0    0               0                 0   
1          0           0       0    0               0                 0   
2          0           0       0    0               0                 0   
3          0           0       0    0               0                 0   
4          0           0       0    0               0                 0   

   Basketball Court  Basketball Stadium  Beach  Beach Bar  Bed & Breakfast  \
0                 0                   0      0          0                0   
1                 0                   0      0          0                0   
2                 0                   0      0          0                0   
3                 0                   0      0          0                0   
4                 0                   0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  Bistro  \
0         0            0           0              0          0       0   
1         0            0           0              0          0       0   
2         0            0           0              0          0       0   
3         0            0           0              0          0       0   
4         0            0           0              0          0       0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0              0          0                 0         0              0   
1              0          0                 0         0              0   
2              0          0                 0         0              0   
3              0          0                 0         0              0   
4              0          0                 0         0              0   

   Bowling Green  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0                     0               0        0   
1              0                     0               0        0   
2              0                     0               0        0   
3              0                     0               0        0   
4              0                     0  

#### Let's group rows by suburbs and by taking the mean of the frequency of occurrence of each category

In [28]:
melb_grouped = melb_onehot.groupby(["Suburb"]).mean().reset_index()

print(melb_grouped.shape)
melb_grouped

(538, 282)


Suburb  Afghan Restaurant  \
0                            Abbotsford               0.00   
1                            Aberfeldie               0.00   
2                               Aintree               0.00   
3                          Airport West               0.00   
4                             Albanvale               0.00   
5                           Albert Park               0.00   
6                                Albion               0.00   
7                            Alphington               0.02   
8                                Altona               0.00   
9                        Altona Meadows               0.00   
10                         Altona North               0.00   
11                               Ardeer               0.00   
12                             Armadale               0.00   
13                         Arthurs Seat               0.00   
14                           Ascot Vale               0.00   
15                            Ashburton               0.00   
16                              Ashwood               0.00   
17                            Aspendale               0.00   
18                    Aspendale Gardens               0.00   
19                              Attwood               0.00   
20                     Avondale Heights               0.00   
21                           Avonsleigh               0.00   
22                         Badger Creek               0.00   
23                            Balaclava               0.00   
24                           Balnarring               0.00   
25                     Balnarring Beach               0.00   
26                               Balwyn               0.00   
27                         Balwyn North               0.00   
28                            Bangholme               0.00   
29                               Baxter               0.00   
30                               Bayles               0.00   
31                            Bayswater               0.00   
32                      Bayswater North               0.00   
33                         Beaconsfield               0.00   
34                   Beaconsfield Upper               0.00   
35                            Beaumaris               0.00   
36                               Beenak               0.00   
37                             Belgrave               0.00   
38                     Belgrave Heights               0.00   
39                       Belgrave South               0.00   
40                            Bellfield               0.00   
41                      Bend of Islands               0.00   
42                            Bentleigh               0.00   
43                       Bentleigh East               0.00   
44                              Berwick               0.00   
45                            Beveridge               0.02   
46                       Big Pats Creek               0.00   
47                              Bittern               0.00   
48                           Black Rock               0.00   
49                            Blackburn               0.00   
50                      Blackburn North               0.00   
51                      Blackburn South               0.00   
52                          Blairgowrie               0.00   
53                          Blind Bight               0.00   
54                             Bonbeach               0.00   
55                                Boneo               0.00   
56                         Bonnie Brook               0.00   
57                              Boronia               0.00   
58                        Botanic Ridge               0.00   
59                             Box Hill               0.00   
60                       Box Hill North               0.00   
61                       Box Hill South               0.00   
62                             Braeside               0.00   
63                            Braybrook               0.00   
64 

In [29]:
len(melb_grouped[melb_grouped["Pizza Place"] > 0])

289

In [30]:
melb_ital = melb_grouped[["Suburb","Pizza Place"]]

In [31]:
melb_ital.head()

Suburb  Pizza Place
0    Abbotsford     0.060000
1    Aberfeldie     0.028571
2       Aintree     0.020000
3  Airport West     0.000000
4     Albanvale     0.000000

## Cluster suburbs

In [32]:
# no. of clusters
kclusters = 3

melb_clustering = melb_ital.drop(["Suburb"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(melb_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 2, 2, 0, 0, 2, 0, 0, 0, 0], dtype=int32)

In [33]:
# Create new dataframe including the cluster label

melb_merged = melb_ital.copy()

# add clustering labels
melb_merged["Cluster Labels"] = kmeans.labels_

In [34]:
melb_merged.set_index(['Suburb'])
melb_merged.head()

Suburb  Pizza Place  Cluster Labels
0    Abbotsford     0.060000               1
1    Aberfeldie     0.028571               2
2       Aintree     0.020000               2
3  Airport West     0.000000               0
4     Albanvale     0.000000               0

In [35]:
# Merge with the neighborhood datframe to get latitude/longitude for each neighborhood
melb_merged = melb_merged.join(df.set_index("Suburb"), on="Suburb")

In [36]:
melb_merged.shape
melb_merged.head()

Suburb  Pizza Place  Cluster Labels   Latitude   Longitude
0    Abbotsford     0.060000               1 -37.776843  145.029515
1    Aberfeldie     0.028571               2 -38.182980  145.090250
2       Aintree     0.020000               2 -37.899664  144.649732
3  Airport West     0.000000               0 -37.786250  145.381630
4     Albanvale     0.000000               0 -37.875150  145.306296

In [37]:
melb_merged.sort_values(["Cluster Labels"], inplace=True)
melb_merged

Suburb  Pizza Place  Cluster Labels  \
268                          Kingsville     0.000000               0   
311                             Mentone     0.000000               0   
310                         Melton West     0.000000               0   
309                        Melton South     0.000000               0   
308                              Melton     0.000000               0   
307  Melbourne CBD (St Kilda Road area)     0.000000               0   
304                      Meadow Heights     0.000000               0   
303                      McMahons Creek     0.000000               0   
301                              McCrae     0.000000               0   
300                             Matlock     0.000000               0   
295                        Malvern East     0.000000               0   
293                          Main Ridge     0.000000               0   
285                        Lower Plenty     0.000000               0   
280                            Laverton     0.000000               0   
278                    Langwarrin South     0.000000               0   
277                          Langwarrin     0.000000               0   
269                           Knoxfield     0.000000               0   
536                          Yarraville     0.000000               0   
313                              Mernda     0.000000               0   
266                          Kings Park     0.000000               0   
316                      Merricks North     0.000000               0   
318                         Middle Park     0.000000               0   
343                   Mount Toolebewong     0.000000               0   
342                        Mount Martha     0.000000               0   
341                        Mount Evelyn     0.000000               0   
340                         Mount Eliza     0.000000               0   
339                     Mount Dandenong     0.000000               0   
338                      Mount Cottrell     0.000000               0   
337                       Mount Burnett     0.000000               0   
336                          Mornington     0.000000               0   
334                         Mooroolbark     0.000000               0   
332                   Moorabbin Airport     0.000000               0   
330                        Moonee Ponds     0.000000               0   
328                         Montmorency     0.000000               0   
326                         Mont Albert     0.000000               0   
323                   Monash University     0.000000               0   
322                             Modella     0.000000               0   
321                             Mitcham     0.000000               0   
319                           Mill Park     0.000000               0   
317                           Mickleham     0.000000               0   
346                         Murrumbeena     0.000000               0   
264                            Kinglake     0.000000               0   
262                             Kilsyth     0.000000               0   
216                       HMAS Cerberus     0.000000               0   
215                           Guys Hill     0.000000               0   
214                             Gruyere     0.000000               0   
213                           Greenvale     0.000000               0   
209                             Glenroy     0.000000               0   
207                           Glen Iris     0.000000               0   
204                      Gladstone Park     0.000000               0   
201                      Garfield North     0.000000               0   
198                         Fraser Rise     0.000000               0   
197                     Frankston South     0.000000               0   
193                           Footscray     0.000000               0   
188                              Fingal     0.000000               0   
1

### Visualizing

In [38]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(melb_merged['Latitude'], melb_merged['Longitude'], melb_merged['Suburb'], melb_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Understanding clusters

In [39]:
# Cluster 0
melb_merged.loc[melb_merged['Cluster Labels'] == 0]

Suburb  Pizza Place  Cluster Labels  \
268                          Kingsville          0.0               0   
311                             Mentone          0.0               0   
310                         Melton West          0.0               0   
309                        Melton South          0.0               0   
308                              Melton          0.0               0   
307  Melbourne CBD (St Kilda Road area)          0.0               0   
304                      Meadow Heights          0.0               0   
303                      McMahons Creek          0.0               0   
301                              McCrae          0.0               0   
300                             Matlock          0.0               0   
295                        Malvern East          0.0               0   
293                          Main Ridge          0.0               0   
285                        Lower Plenty          0.0               0   
280                            Laverton          0.0               0   
278                    Langwarrin South          0.0               0   
277                          Langwarrin          0.0               0   
269                           Knoxfield          0.0               0   
536                          Yarraville          0.0               0   
313                              Mernda          0.0               0   
266                          Kings Park          0.0               0   
316                      Merricks North          0.0               0   
318                         Middle Park          0.0               0   
343                   Mount Toolebewong          0.0               0   
342                        Mount Martha          0.0               0   
341                        Mount Evelyn          0.0               0   
340                         Mount Eliza          0.0               0   
339                     Mount Dandenong          0.0               0   
338                      Mount Cottrell          0.0               0   
337                       Mount Burnett          0.0               0   
336                          Mornington          0.0               0   
334                         Mooroolbark          0.0               0   
332                   Moorabbin Airport          0.0               0   
330                        Moonee Ponds          0.0               0   
328                         Montmorency          0.0               0   
326                         Mont Albert          0.0               0   
323                   Monash University          0.0               0   
322                             Modella          0.0               0   
321                             Mitcham          0.0               0   
319                           Mill Park          0.0               0   
317                           Mickleham          0.0               0   
346                         Murrumbeena          0.0               0   
264                            Kinglake          0.0               0   
262                             Kilsyth          0.0               0   
216                       HMAS Cerberus          0.0               0   
215                           Guys Hill          0.0               0   
214                             Gruyere          0.0               0   
213                           Greenvale          0.0               0   
209                             Glenroy          0.0               0   
207                           Glen Iris          0.0               0   
204                      Gladstone Park          0.0               0   
201                      Garfield North          0.0               0   
198                         Fraser Rise          0.0               0   
197                     Frankston South          0.0               0   
193                           Footscray          0.0               0   
188                              Fingal          0.0               0   
1

In [40]:
# Cluster 1
melb_merged.loc[melb_merged['Cluster Labels'] == 1]

Suburb  Pizza Place  Cluster Labels   Latitude   Longitude
376        Pakenham Upper     0.060000               1 -37.768261  145.027638
372                Olinda     0.040000               1 -37.857400  144.737880
350          Narre Warren     0.040000               1 -38.074640  145.275620
85            Caldermeade     0.040000               1 -37.730080  144.756250
352    Narre Warren North     0.045455               1 -38.124550  145.248570
369        Oakleigh South     0.066667               1 -38.061570  145.258174
349    Nar Nar Goon North     0.106383               1 -38.048110  145.113960
360             Northcote     0.040000               1 -37.769230  144.775060
168           Elsternwick     0.040000               1 -38.036750  145.114380
362            Nunawading     0.040000               1 -37.730070  144.815710
333             Moorooduc     0.040000               1 -37.758390  144.743480
103       Caulfield North     0.040000               1 -37.764210  145.067560
366     Oaklands Junction     0.040000               1 -37.780441  145.065299
97       Caroline Springs     0.047619               1 -38.355948  144.932519
98                 Carrum     0.040000               1 -38.033900  145.265750
77           Bunyip North     0.040000               1 -37.761280  144.754800
324               Monbulk     0.040000               1 -37.675900  144.884480
314              Merricks     0.060000               1 -37.741440  145.003440
364                 Nyora     0.061224               1 -38.045140  145.136810
169                Eltham     0.040000               1 -37.744600  144.770250
70              Brunswick     0.060000               1 -38.063060  145.299530
28              Bangholme     0.040000               1 -37.774510  145.018870
480        Tooradin North     0.040000               1 -37.846915  144.677040
493  Upper Ferntree Gully     0.040000               1 -37.772640  145.057980
495               Vermont     0.045455               1 -38.072769  145.127340
18      Aspendale Gardens     0.040000               1 -38.007240  145.279020
498              Viewbank     0.040000               1 -38.026660  145.102020
499           Wandin East     0.047619               1 -37.629290  145.153350
502        Wantirna South     0.045455               1 -38.134280  145.294840
30                 Bayles     0.043478               1 -37.716441  144.734597
506            Warrandyte     0.045455               1 -37.668940  144.765690
510              Watsonia     0.040000               1 -38.018220  145.113590
511        Watsonia North     0.040000               1 -37.669910  144.887920
14             Ascot Vale     0.041667               1 -38.275481  145.030648
513           Wattle Glen     0.040000               1 -37.777647  144.801120
13           Arthurs Seat     0.040000               1 -38.074090  145.145210
523              Wildwood     0.037037               1 -38.020610  145.385470
528               Wollert     0.060000               1 -37.701810  144.762890
530             Woodstock     0.048780               1 -37.837700  144.672900
508            Warranwood     0.040000               1 -37.862310  144.769760
379              Parkdale     0.060000               1 -37.752820  145.050470
470             The Basin     0.080000               1 -37.766360  145.045400
34     Beaconsfield Upper     0.043478               1 -37.716441  144.734597
384       Patterson Lakes     0.040000               1 -37.747920  145.041670
69               Brooklyn     0.040000               1 -37.817780  145.154140
394               Preston     0.040000               1 -37.719780  144.770630
61         Box Hill South     0.040000               1 -38.057919  145.286615
405         Ringwood East     0.051282               1 -38.182590  145.185000
407             Ripponlea     0.037037               1 -38.102720  145.198840
412         Roxburgh Park     0.040000               1 -37.657517  144.896149
56           Bonnie Brook     0.058824   

In [41]:
# Cluster 2
melb_merged.loc[melb_merged['Cluster Labels'] == 2]

Suburb  Pizza Place  Cluster Labels   Latitude   Longitude
45            Beveridge     0.020000               2 -37.787590  144.832470
31            Bayswater     0.023256               2 -37.688570  144.745180
474      Thornhill Park     0.020000               2 -37.815060  145.193560
443          Springvale     0.032258               2 -38.106234  145.187910
442           Spotswood     0.020000               2 -38.138795  145.158694
453          Strathewen     0.020000               2 -38.113100  145.137420
475       Three Bridges     0.020000               2 -37.770353  145.280355
151            Dewhurst     0.020000               2 -37.836300  145.062510
477            Toolangi     0.020000               2 -37.867780  144.843770
29               Baxter     0.020000               2 -37.597396  144.936400
440         South Yarra     0.020000               2 -37.852490  145.036550
232  Heidelberg Heights     0.020408               2 -37.863820  144.824820
437     South Melbourne     0.020000               2 -37.642940  144.947850
472          Thomastown     0.023810               2 -37.642799  144.824657
150       Devon Meadows     0.020000               2 -37.774300  145.274790
444    Springvale South     0.032258               2 -37.618605  145.000409
217            Hadfield     0.020000               2 -37.902980  145.142540
40            Bellfield     0.020000               2 -37.803060  144.997180
457             Sunbury     0.020000               2 -37.882980  145.165140
222            Harkaway     0.020000               2 -37.768700  145.298030
448           St Helena     0.020000               2 -37.866910  145.102920
221        Hampton Park     0.020000               2 -37.599500  144.945480
220        Hampton East     0.027027               2 -38.032650  145.177390
458            Sunshine     0.020000               2 -37.909370  144.997460
44              Berwick     0.020000               2 -37.815003  144.963977
465        Taylors Hill     0.020000               2 -38.058383  145.340501
144     Dandenong South     0.020000               2 -37.718950  144.894660
452        Steels Creek     0.020000               2 -37.883840  144.623650
467              Tecoma     0.020000               2 -37.856600  145.184300
33         Beaconsfield     0.020000               2 -37.768500  144.975740
454          Strathmore     0.020000               2 -38.020370  145.306210
41      Bend of Islands     0.020000               2 -37.742730  145.065280
445           St Albans     0.020000               2 -37.699910  145.115000
108          Cheltenham     0.020000               2 -37.738888  144.766601
154     Dingley Village     0.020000               2 -37.830280  145.055520
189             Fitzroy     0.023256               2 -37.836230  144.707230
187          Fieldstone     0.020000               2 -37.814260  144.963070
162             Doveton     0.020000               2 -37.799280  144.987550
183             Fawkner     0.020000               2 -37.800540  144.946090
11               Ardeer     0.020000               2 -37.968930  145.030700
518      West Footscray     0.020000               2 -37.733850  144.777050
519      West Melbourne     0.020000               2 -37.875290  145.048310
520         Westmeadows     0.020000               2 -37.854750  145.052220
181           Eynesbury     0.020000               2 -37.670060  144.849340
180              Exford     0.020000               2 -37.638850  144.914820
190       Fitzroy North     0.022222               2 -38.377768  144.850169
178       Essendon West     0.020000               2 -37.886616  145.072316
177      Essendon North     0.020000               2 -37.897700  145.069940
5           Albert Park     0.020000               2 -37.732711  144.774018
175            Essendon     0.020000               2 -37.883970  145.127490
529          Wonga Park     0.020000               2 -37.794210  144.927540
173     Endeavour Hills     0.020000               2 -37.663220  

In [42]:
cluster_0 = melb_merged.loc[melb_merged['Cluster Labels'] == 0]
len_cluster_0 = len(cluster_0)

cluster_1 = melb_merged.loc[melb_merged['Cluster Labels'] == 1]
len_cluster_1 = len(cluster_1)

cluster_2 = melb_merged.loc[melb_merged['Cluster Labels'] == 2]
len_cluster_2 = len(cluster_2)

print('Total suburbs in cluster 0 =', len_cluster_0)
print('Total suburbs in cluster 1 =', len_cluster_1)
print('Total suburbs in cluster 2 =', len_cluster_2)

Total suburbs in cluster 0 = 249
Total suburbs in cluster 1 = 102
Total suburbs in cluster 2 = 187


## Observations and analysis:

The results from the k-means clustering shows we can categorize suburbs in 3 clusters based on the frequency of occurrence for “Italian restaurant”:

• Cluster 0 (red in map): Suburbs with low concentration of pizza places; around 46%

• Cluster 1 (blue in map): Suburbs with high concentration of pizza places; around 19%

• Cluster 2 (green in map): Suburbs with medium pizza places; around 35%

Analysis shows that most pizza places are clustered around mid city. This is just where the commercial areas end and the residential areas begin. One exception to that is Brunswick, where there is the famous Lygon street full of Italian restaurants and pizza places.

If a person were to open a pizza place in Melbourne, according to me the place should be somewhere in cluster 1, where there is a high concentration on pizza places. A high concentration of pizza places suggests that there is a high demand for pizza in those aread. However, a high concentration also means high competition. So one must open a pizza place where there is a high demand and then differentiate the product offering in a way that is able to beat the competition and stand out. So, I would suggest that a person should open a pizza place on Lygon street in Brunswick with a highly differentiated and competitive product offering.